# Service 1

In [1]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 14.6 MB/s eta 0:00:00


In [6]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service1.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated']]
y = df[['cpu_usage_pct', 'memory_usage_pct']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300,0.25,500, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Usage: {predicted_allocation[0]}")


[I 2025-05-05 08:04:49,692] A new study created in memory with name: no-name-97b8d8f4-ca8e-40d6-a953-55d9b751b45a
[I 2025-05-05 08:04:49,907] Trial 0 finished with value: 0.09628108155164627 and parameters: {'n_estimators': 127, 'learning_rate': 0.03611769541717268, 'num_leaves': 26, 'max_depth': 12, 'subsample': 0.658128197983751, 'colsample_bytree': 0.6309759624047485, 'reg_alpha': 0.6374938622280073, 'reg_lambda': 0.7701499181309133}. Best is trial 0 with value: 0.09628108155164627.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000367 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:04:50,314] Trial 1 finished with value: 0.011267960931445638 and parameters: {'n_estimators': 365, 'learning_rate': 0.2933056042943588, 'num_leaves': 121, 'max_depth': 4, 'subsample': 0.7346055117222814, 'colsample_bytree': 0.7853114679128281, 'reg_alpha': 0.21429007261941468, 'reg_lambda': 0.4814333896149515}. Best is trial 1 with value: 0.011267960931445638.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2025-05-05 08:04:51,387] Trial 2 finished with value: 0.007873237988096337 and parameters: {'n_estimators': 489, 'learning_rate': 0.1500556959834211, 'num_leaves': 61, 'max_depth': 14, 'subsample': 0.9301620374275623, 'colsample_bytree': 0.7263926091116396, 'reg_alpha': 0.7901749806494642, 'reg_lambda': 0.8582584987415753}. Best is trial 2 with value: 0.007873237988096337.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000383 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:05:30,178] Trial 28 finished with value: 0.006435599194184212 and parameters: {'n_estimators': 983, 'learning_rate': 0.015780764961006704, 'num_leaves': 157, 'max_depth': 6, 'subsample': 0.9661895129645076, 'colsample_bytree': 0.9263342714640617, 'reg_alpha': 0.2608536872235107, 'reg_lambda': 0.11793313393359225}. Best is trial 22 with value: 0.006380559467229452.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000397 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:05:31,850] Trial 29 finished with value: 0.006560227732706498 and parameters: {'n_estimators': 968, 'learning_rate': 0.03734745066869457, 'num_leaves': 155, 'max_depth': 11, 'subsample': 0.843451925864355, 'colsample_bytree': 0.6002968206329851, 'reg_alpha': 0.6113831912811902, 'reg_lambda': 0.37257997057277914}. Best is trial 22 with value: 0.006380559467229452.


Best Parameters: {'n_estimators': 770, 'learning_rate': 0.015855613588525372, 'num_leaves': 188, 'max_depth': 5, 'subsample': 0.9632696752264678, 'colsample_bytree': 0.9977075054741991, 'reg_alpha': 0.197959653342692, 'reg_lambda': 0.017509772203839313}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000772 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 8500, number of used features: 5
[LightGBM] [Info] Start training from score 50.128218
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No furthe

# Service 2

In [5]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service2.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated']]
y = df[['cpu_usage_pct', 'memory_usage_pct']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300,0.25, 500, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Usage: {predicted_allocation[0]}")


[I 2025-05-05 08:02:14,589] A new study created in memory with name: no-name-83316fd8-ba07-4e0f-bab5-cfa33be5d688


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000898 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:02:16,712] Trial 0 finished with value: 0.006559817580318834 and parameters: {'n_estimators': 677, 'learning_rate': 0.06443717362452926, 'num_leaves': 136, 'max_depth': 12, 'subsample': 0.8359330119923397, 'colsample_bytree': 0.884209912124461, 'reg_alpha': 0.9048981978917509, 'reg_lambda': 0.1867427975048952}. Best is trial 0 with value: 0.006559817580318834.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000620 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:02:17,942] Trial 1 finished with value: 0.007823335263445126 and parameters: {'n_estimators': 283, 'learning_rate': 0.14790380764521358, 'num_leaves': 102, 'max_depth': 11, 'subsample': 0.9258368924249241, 'colsample_bytree': 0.9194368875360539, 'reg_alpha': 0.20723788965309753, 'reg_lambda': 0.6980368364154194}. Best is trial 0 with value: 0.006559817580318834.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000646 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [I

[I 2025-05-05 08:03:04,459] Trial 28 finished with value: 0.0069099125860362445 and parameters: {'n_estimators': 637, 'learning_rate': 0.07024564110781378, 'num_leaves': 181, 'max_depth': 9, 'subsample': 0.9439631981175118, 'colsample_bytree': 0.8560947267236952, 'reg_alpha': 0.3944835404095853, 'reg_lambda': 0.2923293447869185}. Best is trial 12 with value: 0.00641937158375376.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000397 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 08:03:05,689] Trial 29 finished with value: 0.006781085373387109 and parameters: {'n_estimators': 704, 'learning_rate': 0.06325653594254085, 'num_leaves': 118, 'max_depth': 10, 'subsample': 0.8091495188172712, 'colsample_bytree': 0.88953538029684, 'reg_alpha': 0.8446139675704432, 'reg_lambda': 0.43918192445141657}. Best is trial 12 with value: 0.00641937158375376.


Best Parameters: {'n_estimators': 998, 'learning_rate': 0.010327437994949635, 'num_leaves': 198, 'max_depth': 8, 'subsample': 0.7600204766099731, 'colsample_bytree': 0.9979381164302811, 'reg_alpha': 0.6737135165662455, 'reg_lambda': 0.24040041981631607}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000806 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 8500, number of used features: 5
[LightGBM] [Info] Start training from score 50.128218
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No furthe